In [6]:
import pandas as pd
import numpy as np

from surprise import Dataset
from surprise import Reader

pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)

In [2]:
# load data
articles = pd.read_csv('./data/articles.csv')
customers = pd.read_csv('./data/customers.csv')
transactions_train = pd.read_csv('./data/sept_2020.csv')

In [3]:
# data features
print(transactions_train.shape)
transactions_train.head()

(798269, 8)


Unnamed: 0       t_dat                                        customer_id  \
0    30990055  2020-09-01  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   
1    30990056  2020-09-01  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   
2    30990057  2020-09-01  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   
3    30990058  2020-09-01  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   
4    30990059  2020-09-01  0005ed68483efa39644c45185550a82dd09acb07622acb...   

   article_id     price  sales_channel_id  year  month  
0   777148006  0.013542                 1  2020      9  
1   835801001  0.018627                 1  2020      9  
2   923134005  0.012695                 1  2020      9  
3   865929003  0.016932                 1  2020      9  
4   863646004  0.033881                 1  2020      9

In [4]:
# rating as the number of purchases for the item by a customer
article_trans = pd.DataFrame(transactions_train.groupby(['customer_id', 'article_id']).count()['t_dat']).reset_index().rename(columns={'t_dat': 'article_rating'})
article_trans.head()

customer_id  article_id  \
0  00000dbacae5abe5e23885899a1fa44253a17956c6d1c3...   568601043   
1  000058a12d5b43e67d225668fa1f8d618c13dc232df0ca...   794321007   
2  0000757967448a6cb83efb3ea7a3fb9d418ac7adf2379d...   448509014   
3  0000757967448a6cb83efb3ea7a3fb9d418ac7adf2379d...   719530003   
4  000172a9c322560c849754ffbdfdb2180d408aa7176b94...   685814001   

   article_rating  
0               1  
1               1  
2               1  
3               1  
4               3

In [7]:
article_trans.article_rating.max()

61

In [14]:
# transactions per item
trans_per_item = pd.DataFrame(transactions_train.groupby(['article_id']).count()['customer_id']).reset_index()
# trans_per_item.head()

# remove items that have been purchased fewer than 20 times
filtered_trans_per_item = trans_per_item[trans_per_item.customer_id >= 20]
popular_articles = filtered_trans_per_item.article_id.tolist()

In [15]:
# transactions per user
trans_per_user = pd.DataFrame(transactions_train.groupby(['customer_id']).count()['article_id']).reset_index()
# trans_per_user.head()

# remove individuals that have made fewer than 10 purchases
filtered_trans_per_user = trans_per_user[trans_per_user.article_id >= 10]
busy_users = filtered_trans_per_user.customer_id.tolist()

In [28]:
# filter transactions to only popular articles and busy users
filtered_trans = article_trans[article_trans.article_id.isin(popular_articles)]
filtered_trans = filtered_trans[filtered_trans.customer_id.isin(busy_users)].reset_index()
print(filtered_trans.shape[0])
filtered_trans.head()

175483


index                                        customer_id  article_id  \
0      5  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   572998013   
1      9  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   865929003   
2     11  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   909869004   
3     12  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   923134003   
4     13  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   923134005   

   article_rating  
0               1  
1               1  
2               1  
3               1  
4               1

In [8]:
reader = Reader(rating_scale=(article_trans.article_rating.min(), article_trans.article_rating.max()))

In [18]:
data = Dataset.load_from_df(filtered_trans[["customer_id", "article_id", "article_rating"]], reader)

In [19]:
from surprise import KNNWithMeans

# defaults to 40 neighbors
algo = KNNWithMeans(name='cosine', user_based=True)

In [20]:
trainingSet = data.build_full_trainset()

In [80]:
from surprise.model_selection import train_test_split
trainset, testset = train_test_split(data, test_size=.3)

In [81]:
algo.fit(trainset)

Computing the msd similarity matrix...
Done computing similarity matrix.


In [23]:
# how the user u will predict item i
prediction = algo.predict('0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37', '572998013')
prediction.est

1.2489243972350599

In [92]:
predictions = algo.test(testset)

In [91]:
for i in predictions:
    print(i.r_ui)

1.0
1.0
2.0
2.0
2.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
2.0
4.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
4.0
2.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
2.0
3.0
1.0
1.0
2.0
1.0
1.0
1.0
2.0
1.0
3.0
1.0
1.0
1.0
1.0
1.0
1.0
3.0
1.0
1.0
1.0
1.0
2.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
3.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
3.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
1.0
2.0
1.0
1.0
1.0
1.0
3.0
2.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0


2.0
1.0
2.0
2.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
3.0
1.0
2.0
2.0
1.0
1.0
2.0
4.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
4.0
1.0
1.0
1.0
1.0
2.0
1.0
2.0
2.0
1.0
1.0
2.0
2.0
4.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
5.0
1.0
1.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
2.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
6.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
6.0
1.0
1.0
1.0
2.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
2.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
1.0
1.0
2.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
4.0
1.0
1.0
2.0
1.0
1.0
2.0
2.0
1.0
2.0
1.0
1.0
3.0
2.0
1.0
1.0
3.0
1.0
2.0


1.0
3.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
3.0
2.0
1.0
1.0
2.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
1.0
1.0
4.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
3.0
2.0
1.0
2.0
1.0
1.0
1.0
1.0
2.0
1.0
4.0
2.0
1.0
1.0
2.0
1.0
2.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
2.0
1.0
1.0
1.0
8.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
3.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
4.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
2.0
1.0
3.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
3.0
2.0
1.0
1.0
2.0
1.0
2.0
1.0
1.0
1.0
2.0
1.0
1.0
2.0


1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
3.0
1.0
2.0
1.0
1.0
1.0
1.0
2.0
2.0
1.0
2.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
3.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
2.0
1.0
2.0
1.0
1.0
1.0
1.0
3.0
1.0
1.0
1.0
1.0
1.0
1.0
3.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
2.0
2.0
1.0
2.0
1.0
1.0
2.0
1.0
2.0
1.0
2.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
2.0
1.0
2.0
2.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
2.0
1.0
1.0
2.0
1.0
2.0
1.0
1.0
2.0
2.0
1.0
1.0
2.0
2.0
1.0
2.0
1.0
1.0
1.0
2.0
1.0
1.0
4.0
2.0
2.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
3.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
2.0


3.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
3.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
3.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
2.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
2.0
1.0
2.0
1.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
2.0
2.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
2.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
2.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
2.0
1.0
2.0
1.0
2.0
1.0
3.0
1.0
1.0
3.0
1.0
2.0
1.0
2.0
2.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
2.0
1.0
1.0
1.0
3.0
2.0
1.0
2.0
1.0
2.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0


...

1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
3.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
3.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
2.0
2.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
3.0
2.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
1.0
2.0
1.0
2.0
1.0
1.0
3.0
1.0
1.0
1.0
3.0
1.0
1.0
2.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
3.0
1.0
1.0
2.0
1.0
1.0
2.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
4.0
3.0
1.0
1.0
1.0
1.0


2.0
1.0
2.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
2.0
1.0
1.0
1.0
5.0
2.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
6.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
3.0
4.0
1.0
1.0
2.0
1.0
3.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
3.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
3.0
1.0
1.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
2.0
2.0
1.0
2.0
1.0
1.0
1.0
2.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0


1.0
1.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
1.0
1.0
2.0
1.0
1.0
2.0
1.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
3.0
1.0
1.0
1.0
1.0
2.0
1.0
2.0
2.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
3.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
3.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
2.0
1.0
3.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
2.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
1.0
2.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
3.0
2.0


1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
3.0
1.0
1.0
2.0
1.0
1.0
1.0
3.0
1.0
1.0
2.0
1.0
2.0
1.0
1.0
2.0
1.0
4.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
3.0
3.0
1.0
2.0
1.0
1.0
3.0
1.0
4.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
10.0
1.0
1.0
3.0
2.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
3.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0

11.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
3.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
3.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
5.0
2.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
4.0
1.0
1.0
1.0
3.0
1.0
1.0
3.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
2.0
1.0
1.0
2.0
1.0
2.0
1.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
8.0
2.0
1.0
1.0
1.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
1.0
2.0
2.0
1.0
1.0
1.0
2.0
1.0
1.0
1.0
2.0
1.0
1.0
4.0
2.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0
1.0

In [90]:
predictions[0].r_ui

1.0

In [85]:
from surprise import accuracy
accuracy.rmse(predictions)

RMSE: 0.6755


0.6755133760324746

# Without the already made prediction functions

In [24]:
filtered_trans.customer_id.nunique()

16537

In [37]:
user_predictions = []
for i in range(filtered_trans.shape[0]):
    user_predictions.append(algo.predict(filtered_trans.customer_id[i], filtered_trans.article_id[i]).est)
    print('{}/{} completed'.format(i, filtered_trans.shape[0]))

0/175483 completed
1/175483 completed
2/175483 completed
3/175483 completed
4/175483 completed
5/175483 completed
6/175483 completed
7/175483 completed
8/175483 completed
9/175483 completed
10/175483 completed
11/175483 completed
12/175483 completed
13/175483 completed
14/175483 completed
15/175483 completed
16/175483 completed
17/175483 completed
18/175483 completed
19/175483 completed
20/175483 completed
21/175483 completed
22/175483 completed
23/175483 completed
24/175483 completed
25/175483 completed
26/175483 completed
27/175483 completed
28/175483 completed
29/175483 completed
30/175483 completed
31/175483 completed
32/175483 completed
33/175483 completed
34/175483 completed
35/175483 completed
36/175483 completed
37/175483 completed
38/175483 completed
39/175483 completed
40/175483 completed
41/175483 completed
42/175483 completed
43/175483 completed
44/175483 completed
45/175483 completed
46/175483 completed
47/175483 completed
48/175483 completed
49/175483 completed
50/175483 

484/175483 completed
485/175483 completed
486/175483 completed
487/175483 completed
488/175483 completed
489/175483 completed
490/175483 completed
491/175483 completed
492/175483 completed
493/175483 completed
494/175483 completed
495/175483 completed
496/175483 completed
497/175483 completed
498/175483 completed
499/175483 completed
500/175483 completed
501/175483 completed
502/175483 completed
503/175483 completed
504/175483 completed
505/175483 completed
506/175483 completed
507/175483 completed
508/175483 completed
509/175483 completed
510/175483 completed
511/175483 completed
512/175483 completed
513/175483 completed
514/175483 completed
515/175483 completed
516/175483 completed
517/175483 completed
518/175483 completed
519/175483 completed
520/175483 completed
521/175483 completed
522/175483 completed
523/175483 completed
524/175483 completed
525/175483 completed
526/175483 completed
527/175483 completed
528/175483 completed
529/175483 completed
530/175483 completed
531/175483 co

979/175483 completed
980/175483 completed
981/175483 completed
982/175483 completed
983/175483 completed
984/175483 completed
985/175483 completed
986/175483 completed
987/175483 completed
988/175483 completed
989/175483 completed
990/175483 completed
991/175483 completed
992/175483 completed
993/175483 completed
994/175483 completed
995/175483 completed
996/175483 completed
997/175483 completed
998/175483 completed
999/175483 completed
1000/175483 completed
1001/175483 completed
1002/175483 completed
1003/175483 completed
1004/175483 completed
1005/175483 completed
1006/175483 completed
1007/175483 completed
1008/175483 completed
1009/175483 completed
1010/175483 completed
1011/175483 completed
1012/175483 completed
1013/175483 completed
1014/175483 completed
1015/175483 completed
1016/175483 completed
1017/175483 completed
1018/175483 completed
1019/175483 completed
1020/175483 completed
1021/175483 completed
1022/175483 completed
1023/175483 completed
1024/175483 completed
1025/1754

1469/175483 completed
1470/175483 completed
1471/175483 completed
1472/175483 completed
1473/175483 completed
1474/175483 completed
1475/175483 completed
1476/175483 completed
1477/175483 completed
1478/175483 completed
1479/175483 completed
1480/175483 completed
1481/175483 completed
1482/175483 completed
1483/175483 completed
1484/175483 completed
1485/175483 completed
1486/175483 completed
1487/175483 completed
1488/175483 completed
1489/175483 completed
1490/175483 completed
1491/175483 completed
1492/175483 completed
1493/175483 completed
1494/175483 completed
1495/175483 completed
1496/175483 completed
1497/175483 completed
1498/175483 completed
1499/175483 completed
1500/175483 completed
1501/175483 completed
1502/175483 completed
1503/175483 completed
1504/175483 completed
1505/175483 completed
1506/175483 completed
1507/175483 completed
1508/175483 completed
1509/175483 completed
1510/175483 completed
1511/175483 completed
1512/175483 completed
1513/175483 completed
1514/17548

2008/175483 completed
2009/175483 completed
2010/175483 completed
2011/175483 completed
2012/175483 completed
2013/175483 completed
2014/175483 completed
2015/175483 completed
2016/175483 completed
2017/175483 completed
2018/175483 completed
2019/175483 completed
2020/175483 completed
2021/175483 completed
2022/175483 completed
2023/175483 completed
2024/175483 completed
2025/175483 completed
2026/175483 completed
2027/175483 completed
2028/175483 completed
2029/175483 completed
2030/175483 completed
2031/175483 completed
2032/175483 completed
2033/175483 completed
2034/175483 completed
2035/175483 completed
2036/175483 completed
2037/175483 completed
2038/175483 completed
2039/175483 completed
2040/175483 completed
2041/175483 completed
2042/175483 completed
2043/175483 completed
2044/175483 completed
2045/175483 completed
2046/175483 completed
2047/175483 completed
2048/175483 completed
2049/175483 completed
2050/175483 completed
2051/175483 completed
2052/175483 completed
2053/17548

...

173525/175483 completed
173526/175483 completed
173527/175483 completed
173528/175483 completed
173529/175483 completed
173530/175483 completed
173531/175483 completed
173532/175483 completed
173533/175483 completed
173534/175483 completed
173535/175483 completed
173536/175483 completed
173537/175483 completed
173538/175483 completed
173539/175483 completed
173540/175483 completed
173541/175483 completed
173542/175483 completed
173543/175483 completed
173544/175483 completed
173545/175483 completed
173546/175483 completed
173547/175483 completed
173548/175483 completed
173549/175483 completed
173550/175483 completed
173551/175483 completed
173552/175483 completed
173553/175483 completed
173554/175483 completed
173555/175483 completed
173556/175483 completed
173557/175483 completed
173558/175483 completed
173559/175483 completed
173560/175483 completed
173561/175483 completed
173562/175483 completed
173563/175483 completed
173564/175483 completed
173565/175483 completed
173566/175483 co

174089/175483 completed
174090/175483 completed
174091/175483 completed
174092/175483 completed
174093/175483 completed
174094/175483 completed
174095/175483 completed
174096/175483 completed
174097/175483 completed
174098/175483 completed
174099/175483 completed
174100/175483 completed
174101/175483 completed
174102/175483 completed
174103/175483 completed
174104/175483 completed
174105/175483 completed
174106/175483 completed
174107/175483 completed
174108/175483 completed
174109/175483 completed
174110/175483 completed
174111/175483 completed
174112/175483 completed
174113/175483 completed
174114/175483 completed
174115/175483 completed
174116/175483 completed
174117/175483 completed
174118/175483 completed
174119/175483 completed
174120/175483 completed
174121/175483 completed
174122/175483 completed
174123/175483 completed
174124/175483 completed
174125/175483 completed
174126/175483 completed
174127/175483 completed
174128/175483 completed
174129/175483 completed
174130/175483 co

174494/175483 completed
174495/175483 completed
174496/175483 completed
174497/175483 completed
174498/175483 completed
174499/175483 completed
174500/175483 completed
174501/175483 completed
174502/175483 completed
174503/175483 completed
174504/175483 completed
174505/175483 completed
174506/175483 completed
174507/175483 completed
174508/175483 completed
174509/175483 completed
174510/175483 completed
174511/175483 completed
174512/175483 completed
174513/175483 completed
174514/175483 completed
174515/175483 completed
174516/175483 completed
174517/175483 completed
174518/175483 completed
174519/175483 completed
174520/175483 completed
174521/175483 completed
174522/175483 completed
174523/175483 completed
174524/175483 completed
174525/175483 completed
174526/175483 completed
174527/175483 completed
174528/175483 completed
174529/175483 completed
174530/175483 completed
174531/175483 completed
174532/175483 completed
174533/175483 completed
174534/175483 completed
174535/175483 co

174985/175483 completed
174986/175483 completed
174987/175483 completed
174988/175483 completed
174989/175483 completed
174990/175483 completed
174991/175483 completed
174992/175483 completed
174993/175483 completed
174994/175483 completed
174995/175483 completed
174996/175483 completed
174997/175483 completed
174998/175483 completed
174999/175483 completed
175000/175483 completed
175001/175483 completed
175002/175483 completed
175003/175483 completed
175004/175483 completed
175005/175483 completed
175006/175483 completed
175007/175483 completed
175008/175483 completed
175009/175483 completed
175010/175483 completed
175011/175483 completed
175012/175483 completed
175013/175483 completed
175014/175483 completed
175015/175483 completed
175016/175483 completed
175017/175483 completed
175018/175483 completed
175019/175483 completed
175020/175483 completed
175021/175483 completed
175022/175483 completed
175023/175483 completed
175024/175483 completed
175025/175483 completed
175026/175483 co

175442/175483 completed
175443/175483 completed
175444/175483 completed
175445/175483 completed
175446/175483 completed
175447/175483 completed
175448/175483 completed
175449/175483 completed
175450/175483 completed
175451/175483 completed
175452/175483 completed
175453/175483 completed
175454/175483 completed
175455/175483 completed
175456/175483 completed
175457/175483 completed
175458/175483 completed
175459/175483 completed
175460/175483 completed
175461/175483 completed
175462/175483 completed
175463/175483 completed
175464/175483 completed
175465/175483 completed
175466/175483 completed
175467/175483 completed
175468/175483 completed
175469/175483 completed
175470/175483 completed
175471/175483 completed
175472/175483 completed
175473/175483 completed
175474/175483 completed
175475/175483 completed
175476/175483 completed
175477/175483 completed
175478/175483 completed
175479/175483 completed
175480/175483 completed
175481/175483 completed
175482/175483 completed


In [38]:
filtered_trans['predicted'] = user_predictions
rmse = np.sqrt((1/filtered_trans.shape[0]) * np.sum((filtered_trans.predicted-filtered_trans.article_rating)**2))
rmse

0.34088100629093343

In [39]:
filtered_trans.head()

index                                        customer_id  article_id  \
0      5  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   572998013   
1      9  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   865929003   
2     11  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   909869004   
3     12  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   923134003   
4     13  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   923134005   

   article_rating  predicted  
0               1        1.0  
1               1        1.0  
2               1        1.0  
3               1        1.0  
4               1        1.0

In [54]:
sort_predictions = filtered_trans.sort_values(by=['customer_id', 'predicted'], ascending=False)
sort_predictions

index                                        customer_id  article_id  \
175481  705492  fffef3b6b73545df065b521e19f64bf6fe93bfd450ab20...   905365002   
175479  705490  fffef3b6b73545df065b521e19f64bf6fe93bfd450ab20...   881919001   
175475  705486  fffef3b6b73545df065b521e19f64bf6fe93bfd450ab20...   748269009   
175477  705488  fffef3b6b73545df065b521e19f64bf6fe93bfd450ab20...   863646005   
175476  705487  fffef3b6b73545df065b521e19f64bf6fe93bfd450ab20...   803757023   
...        ...                                                ...         ...   
0            5  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   572998013   
1            9  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   865929003   
2           11  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   909869004   
3           12  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   923134003   
4           13  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   923134005   

        article_rating  predicted  
175481               2   1.638793  
175479               2   1.445412  
175475               2   1.395357  
175477               1   1.262102  
175476               1   1.207024  
...                ...        ...  
0                    1   1.000000  
1                    1   1.000000  
2                    1   1.000000  
3                    1   1.000000  
4                    1   1.000000  

[81145 rows x 5 columns]

In [55]:
top_5_preds = sort_predictions.groupby('customer_id').head(5) 
top_5_preds

index                                        customer_id  article_id  \
175481  705492  fffef3b6b73545df065b521e19f64bf6fe93bfd450ab20...   905365002   
175479  705490  fffef3b6b73545df065b521e19f64bf6fe93bfd450ab20...   881919001   
175475  705486  fffef3b6b73545df065b521e19f64bf6fe93bfd450ab20...   748269009   
175477  705488  fffef3b6b73545df065b521e19f64bf6fe93bfd450ab20...   863646005   
175476  705487  fffef3b6b73545df065b521e19f64bf6fe93bfd450ab20...   803757023   
...        ...                                                ...         ...   
0            5  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   572998013   
1            9  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   865929003   
2           11  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   909869004   
3           12  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   923134003   
4           13  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   923134005   

        article_rating  predicted  
175481               2   1.638793  
175479               2   1.445412  
175475               2   1.395357  
175477               1   1.262102  
175476               1   1.207024  
...                ...        ...  
0                    1   1.000000  
1                    1   1.000000  
2                    1   1.000000  
3                    1   1.000000  
4                    1   1.000000  

[81145 rows x 5 columns]

In [56]:
recommended_articles = top_5_preds.groupby('customer_id').agg({'article_id': lambda x: x.tolist()}).reset_index()
recommended_articles

customer_id  \
0      0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   
1      000493dd9fc463df1acc2081450c9e75ef8e87d5dd17ed...   
2      00077dbd5c4a4991e092e63893ccf29294a9d5c46e8501...   
3      000fa1b80857fa40bf25990bc1b1b65afc63923a8e4b57...   
4      000fb6e772c5d0023892065e659963da90b1866035558e...   
...                                                  ...   
16532  fff2282977442e327b45d8c89afde25617d00124d0f999...   
16533  fff3573d9131d15da6a46c1ca8f03b5d37e4f6b804171e...   
16534  fff67e0ce3800aab23d16104d8ae13224f80053000dd6e...   
16535  fffae8eb3a282d8c43c77dd2ca0621703b71e90904dfde...   
16536  fffef3b6b73545df065b521e19f64bf6fe93bfd450ab20...   

                                              article_id  
0      [572998013, 865929003, 909869004, 923134003, 9...  
1      [399136061, 556255001, 640021019, 732842014, 7...  
2      [158340001, 448509014, 456163060, 486639003, 7...  
3      [879291001, 685813001, 685813037, 748355018, 7...  
4      [919273004, 927922002, 871519008, 889669006, 9...  
...                                                  ...  
16532  [919365008, 894780001, 918892001, 891322004, 9...  
16533  [918892001, 673677024, 673677023, 783517006, 7...  
16534  [456163087, 769748014, 805000008, 868823007, 8...  
16535  [865624003, 797892001, 914441004, 894320003, 9...  
16536  [905365002, 881919001, 748269009, 863646005, 8...  

[16537 rows x 2 columns]

In [59]:
sort_ratings = filtered_trans.sort_values(by=['customer_id', 'article_rating'], ascending=False)
sort_ratings

index                                        customer_id  article_id  \
175481  705492  fffef3b6b73545df065b521e19f64bf6fe93bfd450ab20...   905365002   
175479  705490  fffef3b6b73545df065b521e19f64bf6fe93bfd450ab20...   881919001   
175475  705486  fffef3b6b73545df065b521e19f64bf6fe93bfd450ab20...   748269009   
175477  705488  fffef3b6b73545df065b521e19f64bf6fe93bfd450ab20...   863646005   
175476  705487  fffef3b6b73545df065b521e19f64bf6fe93bfd450ab20...   803757023   
...        ...                                                ...         ...   
0            5  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   572998013   
1            9  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   865929003   
2           11  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   909869004   
3           12  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   923134003   
4           13  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   923134005   

        article_rating  predicted  
175481               2   1.638793  
175479               2   1.445412  
175475               2   1.395357  
175477               1   1.262102  
175476               1   1.207024  
...                ...        ...  
0                    1   1.000000  
1                    1   1.000000  
2                    1   1.000000  
3                    1   1.000000  
4                    1   1.000000  

[81145 rows x 5 columns]

In [60]:
top_5_purchase = sort_ratings.groupby('customer_id').head(5) 
top_5_purchase

index                                        customer_id  article_id  \
175481  705492  fffef3b6b73545df065b521e19f64bf6fe93bfd450ab20...   905365002   
175479  705490  fffef3b6b73545df065b521e19f64bf6fe93bfd450ab20...   881919001   
175475  705486  fffef3b6b73545df065b521e19f64bf6fe93bfd450ab20...   748269009   
175477  705488  fffef3b6b73545df065b521e19f64bf6fe93bfd450ab20...   863646005   
175476  705487  fffef3b6b73545df065b521e19f64bf6fe93bfd450ab20...   803757023   
...        ...                                                ...         ...   
0            5  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   572998013   
1            9  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   865929003   
2           11  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   909869004   
3           12  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   923134003   
4           13  0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   923134005   

        article_rating  predicted  
175481               2   1.638793  
175479               2   1.445412  
175475               2   1.395357  
175477               1   1.262102  
175476               1   1.207024  
...                ...        ...  
0                    1   1.000000  
1                    1   1.000000  
2                    1   1.000000  
3                    1   1.000000  
4                    1   1.000000  

[81145 rows x 5 columns]

In [62]:
purchased_articles = top_5_purchase.groupby('customer_id').agg({'article_id': lambda x: x.tolist()}).reset_index()
purchased_articles

customer_id  \
0      0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   
1      000493dd9fc463df1acc2081450c9e75ef8e87d5dd17ed...   
2      00077dbd5c4a4991e092e63893ccf29294a9d5c46e8501...   
3      000fa1b80857fa40bf25990bc1b1b65afc63923a8e4b57...   
4      000fb6e772c5d0023892065e659963da90b1866035558e...   
...                                                  ...   
16532  fff2282977442e327b45d8c89afde25617d00124d0f999...   
16533  fff3573d9131d15da6a46c1ca8f03b5d37e4f6b804171e...   
16534  fff67e0ce3800aab23d16104d8ae13224f80053000dd6e...   
16535  fffae8eb3a282d8c43c77dd2ca0621703b71e90904dfde...   
16536  fffef3b6b73545df065b521e19f64bf6fe93bfd450ab20...   

                                              article_id  
0      [572998013, 865929003, 909869004, 923134003, 9...  
1      [399136061, 556255001, 640021019, 732842014, 7...  
2      [158340001, 448509014, 456163060, 486639003, 7...  
3      [879291001, 685813001, 685813037, 748355018, 7...  
4      [919273004, 871519008, 927922002, 889669006, 9...  
...                                                  ...  
16532  [919365008, 891322004, 894780001, 918892001, 9...  
16533  [918892001, 673677024, 673677023, 783517006, 7...  
16534  [456163087, 769748014, 805000008, 868823007, 8...  
16535  [865624003, 797892001, 914441004, 894320003, 9...  
16536  [905365002, 881919001, 748269009, 863646005, 8...  

[16537 rows x 2 columns]

In [65]:
test = purchased_articles.merge(recommended_articles, on='customer_id')
test

customer_id  \
0      0001d44dbe7f6c4b35200abdb052c77a87596fe1bdcc37...   
1      000493dd9fc463df1acc2081450c9e75ef8e87d5dd17ed...   
2      00077dbd5c4a4991e092e63893ccf29294a9d5c46e8501...   
3      000fa1b80857fa40bf25990bc1b1b65afc63923a8e4b57...   
4      000fb6e772c5d0023892065e659963da90b1866035558e...   
...                                                  ...   
16532  fff2282977442e327b45d8c89afde25617d00124d0f999...   
16533  fff3573d9131d15da6a46c1ca8f03b5d37e4f6b804171e...   
16534  fff67e0ce3800aab23d16104d8ae13224f80053000dd6e...   
16535  fffae8eb3a282d8c43c77dd2ca0621703b71e90904dfde...   
16536  fffef3b6b73545df065b521e19f64bf6fe93bfd450ab20...   

                                            article_id_x  \
0      [572998013, 865929003, 909869004, 923134003, 9...   
1      [399136061, 556255001, 640021019, 732842014, 7...   
2      [158340001, 448509014, 456163060, 486639003, 7...   
3      [879291001, 685813001, 685813037, 748355018, 7...   
4      [919273004, 871519008, 927922002, 889669006, 9...   
...                                                  ...   
16532  [919365008, 891322004, 894780001, 918892001, 9...   
16533  [918892001, 673677024, 673677023, 783517006, 7...   
16534  [456163087, 769748014, 805000008, 868823007, 8...   
16535  [865624003, 797892001, 914441004, 894320003, 9...   
16536  [905365002, 881919001, 748269009, 863646005, 8...   

                                            article_id_y  
0      [572998013, 865929003, 909869004, 923134003, 9...  
1      [399136061, 556255001, 640021019, 732842014, 7...  
2      [158340001, 448509014, 456163060, 486639003, 7...  
3      [879291001, 685813001, 685813037, 748355018, 7...  
4      [919273004, 927922002, 871519008, 889669006, 9...  
...                                                  ...  
16532  [919365008, 894780001, 918892001, 891322004, 9...  
16533  [918892001, 673677024, 673677023, 783517006, 7...  
16534  [456163087, 769748014, 805000008, 868823007, 8...  
16535  [865624003, 797892001, 914441004, 894320003, 9...  
16536  [905365002, 881919001, 748269009, 863646005, 8...  

[16537 rows x 3 columns]

In [72]:
map_5 = []
for i in range(test.shape[0]):
    map_5.append(len(set(test.article_id_x[i]).intersection(set(test.article_id_y[i])))/5)

In [74]:
test['map5'] = map_5
test.map5.mean()

0.9813750982644946